# **MACD Trading Strategy for Long Positions**  
## **Backtest Using Pure Returns (No Initial Capital)**  
### **Grid Search Optimization for Parameter Tuning**
---
This analysis implements a MACD-based trading strategy focused exclusively on long positions. It evaluates historical performance using backtests that ignore initial capital, focusing purely on returns. By applying grid search across a range of MACD parameter combinations, the strategy identifies the most effective settings based on historical data – offering a systematic, data-driven approach to optimization.

In [26]:
# Standard library imports
import itertools
import textwrap
import base64
from pathlib import Path

# Core scientific and data manipulation libraries
import numpy as np
import pandas as pd

# Financial data source
import yfinance as yf

# Visualization libraries
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from plotly.io import to_html

# Utility libraries
from tqdm import tqdm

In [27]:
# Graph fonts
# ! You can use any font you like, but make sure to have the font files in the same directory as this script

# Custom fonts -
f_family = "Panton-Regular"
f_bold = "Panton-Bold"
f_black = "Panton-Black"

def encode_font(font_path):
    return base64.b64encode(Path(font_path).read_bytes()).decode("utf-8")

css = f"""
<style>
@font-face {{
    font-family: {f_family};
    src: url(data:font/truetype;charset=utf-8;base64,{encode_font("Fonts/" + f_family + ".ttf")}) format("truetype");
}}
@font-face {{
    font-family: {f_bold};
    src: url(data:font/truetype;charset=utf-8;base64,{encode_font("Fonts/" + f_bold + ".ttf")}) format("truetype");
}}
@font-face {{
    font-family: {f_black};
    src: url(data:font/truetype;charset=utf-8;base64,{encode_font("Fonts/" + f_black + ".ttf")}) format("truetype");
}}
</style>
"""

To fetch stock data, **Yahoo Finance** is used. It makes relatively easy and accesible to retrieve historical stock data.

**Instrument:** you can see the possible tickers of equities (Indices, Commodities, Currencies, Stocks, ETFs, Cryptocurrencies, etc.) directly on the Yahoo Finance website - [Markets Overview](https://finance.yahoo.com/markets/)

**Period:** you can select the period parameter (or the start and end interval) for the lenght of the dataset. The possible periods are 1 day, 5 days, 1 month, 3 months, 6 months, 1 year, 2 years, 5 years, 10 years, year-to-date, or maximum available data. For the start and end interval, use YYYY-MM-DD date format.

**Interval:** you can define how often the data is sampled. The possible intervals are 1 minute, 2 minutes, 5 minutes, 15 minutes, 30 minutes, 1 hour, 90 minutes, 1 day, 5 days, 1 week, 1 month, or 3 months. Intraday data cannot extend last 60 days. *Note that the charts in this code are optimised for daily or larger interval data, still it can calculate strategies correctly.*

In [28]:
# Download historical stock data
# ! You can replace this part if you have different data source

# Instrument ticker
ticker = "CRWD"

# Period
period = "1y"
# Valid periods: 1d, 5d, 1mo, 3mo, 6mo, 1y, 2y, 5y, 10y, ytd, max

# Interval
interval = "1d"
# Valid intervals: 1m, 2m, 5m, 15m, 30m, 60m, 90m, 1h, 4h, 1d, 5d, 1wk, 1mo, 3mo

# Download data using Yahoo Finance
stock_data = yf.download(ticker, period=period, interval=interval, progress=False)
# Or use start date and end date (i.e. start="2024-01-01", end="2025-01-01" instead of period)

# Remove column dimensions - it stores only the equtiy's name
stock_data.columns = stock_data.columns.droplevel(1)

# Company informations
company_info = yf.Ticker(ticker).info

# Period names
period_info = {"1d": "1 day", "5d": "5 days",
                "1mo": "1 month", "3mo": "3 months", "6mo": "6 months",
                "1y": "1 year", "2y": "2 years", "5y": "5 years", "10y": "10 years",
                "ytd": "year-to-date", "max": "maximum available data"}

# Interval names
interval_info = {"1m": "1 minute", "2m": "2 minutes", "5m": "5 minutes", "15m": "15 minutes", "30m": "30 minutes", "60m": "60 minutes", "90m": "90 minutes",
                "1h": "1 hour", "4h": "4 hours",
                "1d": "1 day", "5d": "5 days",
                "1wk": "1 week", "1mo": "1 month", "3mo": "3 months"}

#### **MACD Strategy with Performance Metrics Function**

The core objective of my code is to implementa a **rule-based MACD trading strategy** on historical stock price data and compute a comprehensive set of performance metrics. It simulates trading behavior using realistic assumptions (such as slippage via open-price entries and transaction costs), enabling robust and reproducible backtesting.

---

**Indicator Construction**

The strategy begins with the construction of the **MACD indicator**, a trend-following momentum oscillator:

- A **fast EMA** (default: 12) and a **slow EMA** (default: 26) are calculated from the **Open** prices.
    - *I use the **Open** price for strategy execution to simulate same-bar trading.*
    - *Since MACD is based on Open prices, signals can be computed pre-market, enabling immediate execution at the bar's open.*
- The **MACD line** is the difference between these two EMAs.
- A **Signal line** (default: 9) is applied to the MACD to smooth it.
- The **MACD Histogram**, used for trading signals, is the difference between the MACD line and its Signal line.

After used for calculations, all indicators are rounded for clearer visualization and consistency.

---

**Signal Logic & Position Tracking**

Trading signals are derived from the histogram:

- A **positive histogram** implies bullish momentum → **enter long**.
- A **negative histogram** implies bearish momentum → **exit**.

Trades are detected via changes in histogram polarity. A position is held if the previous histogram was positive, adding robustness to signal continuity.

- **Position**: 1 if in a long position, 0 otherwise.
- **Trades**: +1 for entry, -1 for exit, 0 otherwise.

---

**Execution Pricing Model**

To simulate realistic trade behavior, strategy trades are executed at the **Open** price of the bar where the signal appears:

- On **entry/exit**, the return is based on the **Open** price.
- When holding, return is based on the **Close**.
- Non-position days have no return contribution.

The model is flexible and can easily be adapted to worst/best-case scenarios using the **High** or **Low** prices.

---

**Returns & Cost Adjustments**

- **Strategy return** is calculated only when in position, adjusted for transaction costs at every entry or exit.
- **Daily return** and **cumulative return** are computed for both the raw stock and the strategy.

All returns are expressed in percentage terms for intuitive comparison.

---

**Performance Metrics**

The function outputs a rich set of metrics for evaluation and optimization:

- **Total return** and **average return** of the strategy
- **Volatility** of returns (standard deviation)
- **Number of trades** executed
- **Return efficiency** (return per trade)
- **Win rate**: proportion of trades that are profitable
- **Max drawdown**: deepest equity loss from a peak
- **Sharpe ratio**: annualized risk-adjusted return

Each trade’s return is isolated based on entry/exit index pairs, allowing for clear aggregation of performance per position.

---

**Return Formatting for Plotting**

For easy visualization:

- All percentage-based values (returns, drawdown, etc.) are multiplied by 100 and rounded.
- Price-based columns (Open, Close, EMAs, etc.) are rounded to two decimal places.

---

**Why This Matters**

This function goes beyond simple signal generation — it offers a **realistic, interpretable, and extensible framework** for backtesting:

- Built-in **transaction cost modeling**
- **Precise trade tracking and return simulation**
- Rich **metric set for optimization and benchmarking**
- Clean, extensible logic suitable for layering filters, experimenting with slippage, or integrating into ML workflows

It is especially useful for those seeking **capital-agnostic, systematic evaluation** of momentum-based strategies.

In [29]:
# Define MACD strategy and metrics function
def macd_strategy_metrics(stock_data: pd.DataFrame, fast=12, slow=26, signal=9, transaction_cost_pct=0.0, risk_free_rate=0, periods_per_year=252):
    """
    Applies a MACD-based trading strategy to historical stock data and computes detailed performance metrics.

    Parameters:
    - stock_data (pd.DataFrame): DataFrame containing at least the columns "Open", "Close", "High", and "Low"
    - fast (int): Span for the fast EMA (default: 12)
    - slow (int): Span for the slow EMA (default: 26)
    - signal (int): Span for the MACD signal line EMA (default: 9)
    - transaction_cost_pct (float): Transaction cost as a percentage (e.g., 0.001 for 0.1%)
    - risk_free_rate (float): Annualized risk-free rate used in Sharpe ratio (default: 0)
    - periods_per_year (int): Number of trading periods in a year, e.g., 252 for daily data

    Returns:
    - metrics (dict): Dictionary of performance metrics, including total return, Sharpe ratio, win rate, etc.
    - stock_data (pd.DataFrame): Original DataFrame augmented with columns related to the MACD indicator, signals, 
      trade execution prices, returns, drawdown, and strategy position tracking
    """


    # Strategy -
    # Calculate short (fast) and long (slow) lines, and MACD
    stock_data["Short_EMA"] = stock_data["Open"].ewm(span=fast, adjust=False).mean()
    stock_data["Long_EMA"] = stock_data["Open"].ewm(span=slow, adjust=False).mean()
    stock_data["MACD"] = stock_data["Short_EMA"] - stock_data["Long_EMA"]

    # Calculate Signal Line and MACD Histogram
    stock_data["Signal"] = stock_data["MACD"].ewm(span=signal, adjust=False).mean()
    stock_data["Histogram"] = stock_data["MACD"] - stock_data["Signal"]

    # Trading -
    # Percentage change in stock price
    stock_data["Daily_return"] = stock_data["Close"].pct_change().fillna(0)
    stock_data["Cumulative_daily_return"] = (1 + stock_data["Daily_return"]).cumprod() - 1

    # Generate positions and trades
    stock_data["Position"] = np.where(stock_data["Histogram"] > 0, 1, 0)
    stock_data["Trades"] = stock_data["Position"].diff().fillna(0).astype(int)
    # Hold position for that day if previous histogram was positive
    stock_data.loc[stock_data["Histogram"].shift(1) > 0, "Position"] = 1

    # Calculate strategy price
    stock_data["Strategy_price"] = np.where(stock_data["Position"] == 0, np.nan,
                                            np.where(stock_data["Trades"] == 0, stock_data["Close"], #does not affect the strategy
                                                     np.where(stock_data["Trades"] == 1, stock_data["Open"], #! strategy: "Open"; worst: "High"; best: "Low"
                                                              np.where(stock_data["Trades"] == -1, stock_data["Open"], np.nan)))) #! strategy: "Open"; worst: "Low"; best: "High"
    stock_data["Strategy_return_pure"] = stock_data["Strategy_price"].pct_change(fill_method=None).fillna(0)

    # Apply strategy adjusted with transaction cost
    stock_data["Transaction_cost_pct"] = np.abs(stock_data["Trades"]) * transaction_cost_pct
    stock_data["Strategy_return"] = stock_data["Position"] * (stock_data["Strategy_return_pure"] - stock_data["Transaction_cost_pct"])
    stock_data["Cumulative_strategy_return"] = (1 + stock_data["Strategy_return"]).cumprod() - 1

    # Metrics -
    # Calculate running maximum of cumulative strategy return and drawdown (current cumulative return - peak cumulative return)
    stock_data["Running_max"] = stock_data["Cumulative_strategy_return"].cummax()
    stock_data["Drawdown"] = stock_data["Cumulative_strategy_return"] - stock_data["Running_max"]

    # Positions
    entries = stock_data[stock_data["Trades"] == 1].index
    exits = stock_data[stock_data["Trades"] == -1].index

    position_returns = []
    for entry in entries:
        exit = exits[exits > entry]
        if not exit.empty:
            exit = exit[0]
            position_returns.append((stock_data.loc[entry:exit, "Strategy_return"].add(1).prod() - 1))

    total_positions = len(position_returns)
    profitable_positions = sum(1 for r in position_returns if r > 0)
    losing_positions = sum(1 for r in position_returns if r <= 0)

    tot_return = stock_data["Cumulative_strategy_return"].iloc[-1]
    avg_return = np.mean(position_returns)
    volatility = np.std(position_returns)

    trade_no = stock_data["Trades"].abs().sum()
    tot_return_to_trade_no = tot_return / trade_no if trade_no != 0 else 0
    avg_return_to_trade_no = avg_return / trade_no if trade_no != 0 else 0

    max_drawdown = stock_data["Drawdown"].min()
    sharpe_ratio = ((stock_data["Strategy_return"] - (risk_free_rate / periods_per_year)).mean() / stock_data["Strategy_return"].std()) * np.sqrt(periods_per_year)
    win_rate = profitable_positions/total_positions if total_positions > 0 else 0

    # Store results -
    metrics = {
        "tot_return": tot_return,
        "avg_return": avg_return,
        "volatility": volatility,

        "trade_no": trade_no,
        "tot_return_to_trade_no": tot_return_to_trade_no,
        "avg_return_to_trade_no": avg_return_to_trade_no,

        "total_positions": total_positions,
        "profitable_positions": profitable_positions,
        "losing_positions": losing_positions,

        "max_drawdown": max_drawdown,
        "sharpe_ratio": sharpe_ratio,
        "win_rate": win_rate
    }

    # * Round values for plots -
    stock_data[["Close", "High", "Low", "Open", "Short_EMA", "Long_EMA", "MACD", "Signal", "Histogram"]] = stock_data[["Close", "High", "Low", "Open", "Short_EMA", "Long_EMA", "MACD", "Signal", "Histogram"]].round(2)
    stock_data[["Daily_return", "Cumulative_daily_return", "Transaction_cost_pct", "Strategy_return", "Strategy_return_pure", "Cumulative_strategy_return", "Running_max", "Drawdown"]] = stock_data[["Daily_return", "Cumulative_daily_return", "Transaction_cost_pct", "Strategy_return", "Strategy_return_pure", "Cumulative_strategy_return", "Running_max", "Drawdown"]].mul(100).round(2)

    return metrics, stock_data

In [44]:
# Calculate specific MACD
fast=12
slow=26
signal=9

# Transaction cost: 1,25%
transaction_cost_pct=0.0125
# Risk-free rate: 2% (annualized)
risk_free_rate=0.02
# Trading days in a year: 252
periods_per_year=252
# These parameters are used at the grid search as well!

# Function
metrics, stock_data = macd_strategy_metrics(stock_data=stock_data,
                                            fast=fast, slow=slow, signal=signal,
                                            transaction_cost_pct=transaction_cost_pct,
                                            risk_free_rate=risk_free_rate,
                                            periods_per_year=periods_per_year)

#### **Chart Overview: Price Action & MACD Indicator**

The first chart is a two-panel visualization combining **price movement** and **momentum analysis**:

1. **Top Panel – OHLC & Moving Averages**  
   Displays the asset’s candlestick data (Open, High, Low, Close), overlaid with:
   - A **Fast EMA** (short-term trend)
   - A **Slow EMA** (long-term trend)  
   This helps visualize price trends and potential crossovers that drive the MACD.

2. **Bottom Panel – MACD Indicator**  
   Shows the:
   - **MACD Line** (difference between fast and slow EMA)
   - **Signal Line** (EMA of MACD)
   - **MACD Histogram** (MACD minus Signal)  
   It captures momentum shifts and potential buy/sell signals.

A **zero line** in the MACD subplot highlights when the MACD changes sign — key for identifying bullish or bearish momentum.

In [45]:
# Figure of prices and MACD
# Create a subplot with 2 rows and 1 column
fig = make_subplots(rows=2, cols=1, shared_xaxes=True, 
                    vertical_spacing=0.1, 
                    row_heights=[0.75, 0.25])

hovertemplate_line = "%{x|%Y-%m-%d}, %{y:.2f}<extra></extra>"

# Row 1 -
# OHLC Chart
fig.add_trace(go.Ohlc(x=stock_data.index, xhoverformat="%Y-%m-%d",
                      open=stock_data["Open"],
                      high=stock_data["High"],
                      low=stock_data["Low"],
                      close=stock_data["Close"],
                      name="OHLC"), row=1, col=1)

# Short MA and Long MA Lines
fig.add_trace(go.Scatter(x=stock_data.index, y=stock_data["Short_EMA"], hovertemplate=hovertemplate_line,
                         mode="lines", name="Fast EMA", line=dict(color="#FA8500"), opacity=0.5), row=1, col=1)
fig.add_trace(go.Scatter(x=stock_data.index, y=stock_data["Long_EMA"], hovertemplate=hovertemplate_line,
                         mode="lines", name="Slow EMA", line=dict(color="#203668"), opacity=0.5), row=1, col=1)

# Row 2 -
# MACD Line, Signal Line, and MACD Histogram
fig.add_trace(go.Scatter(x=stock_data.index, y=stock_data["MACD"], hovertemplate=hovertemplate_line,
                         mode="lines", name="MACD Line", line=dict(color="#203668")), row=2, col=1)
fig.add_trace(go.Scatter(x=stock_data.index, y=stock_data["Signal"], hovertemplate=hovertemplate_line,
                         mode="lines", name="Signal Line", line=dict(color="#E5054C")), row=2, col=1)
fig.add_trace(go.Bar(x=stock_data.index, y=stock_data["Histogram"], hovertemplate=hovertemplate_line,
                     name="MACD Histogram", marker_color="gray", opacity=0.5), row=2, col=1)

# Zero Line for MACD
fig.add_hline(y=0, line=dict(color="gray", width=1), row=2, col=1)

# Update -
# Hide non-trading days for both plots
fig.update_xaxes(rangebreaks=[dict(bounds=["sat", "mon"], pattern="day of week")], col=1)

# Update layout
fig.update_layout(
    title=dict(
        text=f"OHLC Chart and MACD Indicator of {company_info['longName']}",
        font=dict(family=f_black, size=20)
    ),


    title_subtitle_text=f"Ticker: {ticker}  |  Period: {period_info[period]}  |  Interval: {interval_info[interval]}",
    title_subtitle_font_family=f_bold,
    title_subtitle_font_color="gray",
    title_subtitle_font_size=16,

    xaxis2_title="<b>Date<b>",
    yaxis1_title="<b>Price<b>",
    yaxis2_title="<b>Value<b>",

    autosize=False,
    height=500, width=1000,

    xaxis_rangeslider_visible=False,
    font=dict(family=f_family),
    template="simple_white",
    margin=dict(l=40, r=40, t=80, b=40)
)

# Annotation -
annotation_text = "<br>".join([
    "<b>MACD Parameters</b>",
    f"Fast: {fast}",
    f"Slow: {slow}",
    f"Signal: {signal}"
])

fig.add_annotation(
    text=annotation_text,
    xref="paper", yref="paper",
    x=1.17, y=0.5,
    showarrow=False,
    align="left",
    font=dict(size=13)
)

# Show the figure -
fig.show()

# Save the figure as an HTML file
with open("Charts/ohclmacd.html", "w") as f:
    f.write(css + to_html(fig, include_plotlyjs="cdn", full_html=True))

#### **Chart Overview: Strategy vs. Market Performance**

This chart visualizes the **cumulative returns** of the MACD trading strategy compared to a simple **buy-and-hold equity approach**:

- **Strategy Performance** and **Equity Performance** lines show how each evolves over time.
- **Open Position markers** indicate when the strategy enters a trade.
- **Close Position markers** show when the trade is exited.

A **horizontal zero line** helps assess when the strategy or equity is in profit or loss territory.  
An accompanying annotation summarizes key performance metrics (e.g., total return, win rate, Sharpe ratio), giving a quick snapshot of the strategy’s effectiveness.

In [46]:
# Figure of Strategy and Returns
fig = go.Figure()

hovertemplate_line = "%{x|%Y-%m-%d}, %{y:.2f}<extra></extra>"

# Zero Line
fig.add_hline(y=0, line=dict(color="black", dash="dash", width=1), layer="below")

# Returns of equity and strategy
fig.add_trace(go.Scatter(x=stock_data.index, y=stock_data["Cumulative_daily_return"], hovertemplate=hovertemplate_line,
                         mode="lines", name="Equity Performance", line=dict(width=2, color="#203668")))
fig.add_trace(go.Scatter(x=stock_data.index, y=stock_data["Cumulative_strategy_return"], hovertemplate=hovertemplate_line,
                         mode="lines", name="Strategy Performance", line=dict(width=2, color="#5ABCC4")))

# Open/Close positions
fig.add_trace(go.Scatter(x=stock_data.index[stock_data["Trades"].shift(-1) == 1],y=stock_data["Cumulative_strategy_return"][stock_data["Trades"].shift(-1) == 1], hovertemplate=hovertemplate_line,
                         mode="markers", name="Open Position", marker=dict(size=6, line=dict(width=2, color="#76A65D"), color="#76A65D", symbol=52)))
fig.add_trace(go.Scatter(x=stock_data.index[stock_data["Trades"].shift(0) == -1],y=stock_data["Cumulative_strategy_return"][stock_data["Trades"].shift(0) == -1], hovertemplate=hovertemplate_line,
                         mode="markers", name="Close Position", marker=dict(size=6, line=dict(width=2, color="#E5054C"), color="#E5054C", symbol=51)))

# Update -
# Hide non-trading days
fig.update_xaxes(rangebreaks=[dict(bounds=["sat", "mon"], pattern="day of week")])

# Update layout
fig.update_layout(

    title=f"MACD Strategy Backtest of {company_info['longName']}",
    title_font_family=f_black,
    title_font_size=20,

    title_subtitle_text=f"Ticker: {ticker}  |  Period: {period_info[period]}  |  Interval: {interval_info[interval]}",
    title_subtitle_font_family=f_bold,
    title_subtitle_font_color="gray",
    title_subtitle_font_size=16,

    xaxis_title="<b>Date<b>",
    yaxis_title="<b>Cumulative Return (%)<b>",

    autosize=False,
    height=500, width=1000,

    xaxis_rangeslider_visible=False,
    font=dict(family=f_family),
    template="simple_white",
    margin=dict(l=40, r=40, t=80, b=40)
)

# Annotation -
annotation_text = "<br>".join([
    "<b>MACD Parameters</b>",
    f"Fast: {fast}",
    f"Slow: {slow}",
    f"Signal: {signal}",
    " ",
    "<b>Strategy Summary</b>",
    f"Total Return: {round(metrics['tot_return'] * 100, 2)}%",
    " ",
    f"Average Return: {round(metrics['avg_return'] * 100, 2)}%",
    f"Volatility: {round(metrics['volatility'] * 100, 2)}%",
    "<i>(per position)</i>",
    " ",
    f"Total Positions: {metrics['total_positions']}",
    f"Profitable Positions: {metrics['profitable_positions']}",
    f"Losing Positions: {metrics['losing_positions']}",
    f"Win Rate: {round(metrics['win_rate'] * 100, 2)}%",
    " ",
    f"Max Drawdown: {round(metrics['max_drawdown'] * 100, 2)}%",
    f"Sharpe Ratio: {round(metrics['sharpe_ratio'], 2)}",
])

fig.add_annotation(
    text=annotation_text,
    xref="paper", yref="paper",
    x=1.2, y=0.725,
    showarrow=False,
    align="left",
    font=dict(size=12)
)

# Show the figure -
fig.show()

# Save the figure as an HTML file
with open("Charts/strategy.html", "w") as f:
    f.write(css + to_html(fig, include_plotlyjs="cdn", full_html=True))

In [33]:
# Generate all combinations of paramteres
max_range = 30
macd_params_results = pd.DataFrame(itertools.product(range(1, max_range+1), range(1, max_range+1), range(1, max_range+1)),
                                   columns=["fast", "slow", "signal"])

# Keep only valid MACD settings (fast < slow), (signal > 1)
macd_params_results = macd_params_results[macd_params_results["fast"] < macd_params_results["slow"]].reset_index(drop=True)
macd_params_results = macd_params_results[macd_params_results["signal"] > 1].reset_index(drop=True)

# Information
print(f"Number of combinations: {len(macd_params_results)}")

Number of combinations: 12615


In [34]:
# Backtests with all parameters
for i in tqdm(range(len(macd_params_results)), desc="Grid search of MACD parameters"):

    # MACD strategy and metrics function
    metrics, stock_data = macd_strategy_metrics(stock_data=stock_data, 
                                                fast=macd_params_results.loc[i, "fast"], 
                                                slow=macd_params_results.loc[i, "slow"], 
                                                signal=macd_params_results.loc[i, "signal"],
                                                transaction_cost_pct=transaction_cost_pct,
                                                risk_free_rate=risk_free_rate,
                                                periods_per_year=periods_per_year)

    # Store results
    macd_params_results.loc[i, list(metrics.keys())] = list(metrics.values())

Grid search of MACD parameters: 100%|██████████| 12615/12615 [00:50<00:00, 251.06it/s]


#### **MACD Strategy Optimization: Parameter Grid Heatmap Analysis**

This chart presents a comprehensive visual analysis of the MACD strategy's performance across a range of parameter configurations, allowing us to explore how the choice of **Fast EMA**, **Slow EMA**, and **Signal EMA** values impacts key performance metrics.

**Structure**
The chart is organized as a **3x3 matrix of heatmaps**, where each subplot highlights a different performance or risk metric derived from the backtest results. These subplots share a common y-axis (**Fast EMA values**) and x-axis (**Slow EMA values**), forming a full grid of parameter combinations.

The metrics visualized are:

- **Top Row:**
  - **Total Return** – The cumulative return of the strategy over the full backtest period.
  - **Average Return** – The mean return per position.
  - **Volatility** – The standard deviation of returns per position, capturing the strategy’s variability or risk.

- **Middle Row:**
  - **Total Return / Trade Count** – A measure of return efficiency, showing how much total return is generated per trade.
  - **Average Return / Trade Count** – Similar to the above, but normalized by average return instead of final outcome.
  - **Trade Count** – Total number of trades executed for each parameter set.

- **Bottom Row:**
  - **Maximum Drawdown** – The largest peak-to-trough loss observed, critical for evaluating downside risk.
  - **Sharpe Ratio** – A standard risk-adjusted return metric, showing return per unit of volatility.
  - **Win Rate** – The percentage of trades that were profitable.

**Interactive Features**
A **slider** along the top allows dynamic adjustment of the **Signal EMA** parameter. When the slider is moved, each heatmap is updated in real-time to reflect results for that specific signal value. This enables quick comparison across slices of the 3D parameter space (Fast × Slow × Signal) without overwhelming the user with separate plots.

**Color Mapping**
A custom colorscale is used across all heatmaps, with a visually intuitive progression from deep purple (low values) to bright yellow(high values), and finally red for the **top 1%** of values. This design highlights optimal zones immediately, making it easy to spot high-performing configurations. For metrics where *lower* is better (e.g. Volatility, Drawdown), the scale is reversed accordingly.

**Interpretation Aid**
To the right of the chart, a detailed annotation explains the meaning of each metric. These annotations break down complex financial terms into accessible definitions, guiding users in interpreting the charts whether they are analysts, developers, or stakeholders with limited financial background.

**Use Case**
This chart is ideal for **hyperparameter tuning**, offering a clear visual method for selecting parameter sets that balance **return, consistency, trade frequency, and risk**. By comparing all metrics simultaneously, it avoids the pitfalls of optimizing for a single metric at the expense of others.

In [39]:
# Figure of Strategies and Results

# Custom colorscale - upper one percent is highlighted
colorscale = [
    [0.00, "#440154"],
    [0.10, "#482777"],
    [0.20, "#3E4A89"],
    [0.30, "#31688E"],
    [0.40, "#26828E"],
    [0.50, "#1F9E89"],
    [0.60, "#35B779"],
    [0.70, "#6DCD59"],
    [0.80, "#AADC32"],
    [0.90, "#F7F100"],
    [0.99, "#F9E200"],
    [1.00, "#E5054C"]
]

# Hover templates for values
hovertemplate_int = "Fast: %{y}<br>Slow: %{x}<br>Value: %{z:.2}<extra></extra>"
hovertemplate_pct = "Fast: %{y}<br>Slow: %{x}<br>Value: %{z:.2%}<extra></extra>"

# Get unique signal values for the slider
unique_signals = sorted(macd_params_results["signal"].unique())

# Create a subplot with 3 rows and 3 columns
fig = make_subplots(rows=3, cols=3, shared_xaxes=True, shared_yaxes=True,
                    vertical_spacing=0.1, horizontal_spacing=0.1,
                    subplot_titles=["<b>Total Return</b>", "<b>Average Return</b>", "<b>Volatility</b>", 
                                    "<b>Total Return / Trade No</b>", "<b>Average Return / Trade No</b>", "<b>Trade Number</b>",
                                    "<b>Drawdown</b>", "<b>Sharpe Ratio</b>", "<b>Win Rate</b>"])

# Figure 1 - Total Return
heatmap_data_lr = macd_params_results[macd_params_results["signal"] == unique_signals[0]].pivot(index="fast", columns="slow", values="tot_return")
fig.add_trace(go.Heatmap(z=heatmap_data_lr.values, x=heatmap_data_lr.columns, y=heatmap_data_lr.index, hovertemplate=hovertemplate_pct,
                        colorscale=colorscale, showscale=False, zmin=heatmap_data_lr.min().min(), zmax=heatmap_data_lr.max().max()), row=1, col=1)

# Figure 2 - Average Return
heatmap_data_ar = macd_params_results[macd_params_results["signal"] == unique_signals[0]].pivot(index="fast", columns="slow", values="avg_return")
fig.add_trace(go.Heatmap(z=heatmap_data_ar.values, x=heatmap_data_ar.columns, y=heatmap_data_ar.index, hovertemplate=hovertemplate_pct,
                        colorscale=colorscale, showscale=False, zmin=heatmap_data_ar.min().min(), zmax=heatmap_data_ar.max().max()), row=1, col=2)

# Figure 3 - Volatility
heatmap_data_vl = macd_params_results[macd_params_results["signal"] == unique_signals[0]].pivot(index="fast", columns="slow", values="volatility")
fig.add_trace(go.Heatmap(z=heatmap_data_vl.values, x=heatmap_data_vl.columns, y=heatmap_data_vl.index, hovertemplate=hovertemplate_pct,
                        colorscale=colorscale, reversescale=True, showscale=False, zmin=heatmap_data_vl.min().min(), zmax=heatmap_data_vl.max().max()), row=1, col=3)

# Figure 4 - Total Return to Trade Number
heatmap_data_lrtn = macd_params_results[macd_params_results["signal"] == unique_signals[0]].pivot(index="fast", columns="slow", values="tot_return_to_trade_no")
fig.add_trace(go.Heatmap(z=heatmap_data_lrtn.values, x=heatmap_data_lrtn.columns, y=heatmap_data_lrtn.index, hovertemplate=hovertemplate_pct,
                        colorscale=colorscale, showscale=False, zmin=heatmap_data_lrtn.min().min(), zmax=heatmap_data_lrtn.max().max()), row=2, col=1)

# Figure 5 - Average Return to Trade Number
heatmap_data_artn = macd_params_results[macd_params_results["signal"] == unique_signals[0]].pivot(index="fast", columns="slow", values="avg_return_to_trade_no")
fig.add_trace(go.Heatmap(z=heatmap_data_artn.values, x=heatmap_data_artn.columns, y=heatmap_data_artn.index, hovertemplate=hovertemplate_pct,
                        colorscale=colorscale, showscale=False, zmin=heatmap_data_artn.min().min(), zmax=heatmap_data_artn.max().max()), row=2, col=2)

# Figure 6 - Trade Number
heatmap_data_tn = macd_params_results[macd_params_results["signal"] == unique_signals[0]].pivot(index="fast", columns="slow", values="trade_no")
fig.add_trace(go.Heatmap(z=heatmap_data_tn.values, x=heatmap_data_tn.columns, y=heatmap_data_tn.index, hovertemplate=hovertemplate_int,
                        colorscale=colorscale, reversescale=True, showscale=False, zmin=heatmap_data_tn.min().min(), zmax=heatmap_data_tn.max().max()), row=2, col=3)

# Figure 7 - Drawdown
heatmap_data_dd = macd_params_results[macd_params_results["signal"] == unique_signals[0]].pivot(index="fast", columns="slow", values="max_drawdown")
fig.add_trace(go.Heatmap(z=heatmap_data_dd.values, x=heatmap_data_dd.columns, y=heatmap_data_dd.index, hovertemplate=hovertemplate_pct,
                        colorscale=colorscale, showscale=False, zmin=heatmap_data_dd.min().min(), zmax=heatmap_data_dd.max().max()), row=3, col=1)

# Figure 8 - Sharpe Ratio
heatmap_data_shr = macd_params_results[macd_params_results["signal"] == unique_signals[0]].pivot(index="fast", columns="slow", values="sharpe_ratio")
fig.add_trace(go.Heatmap(z=heatmap_data_shr.values, x=heatmap_data_shr.columns, y=heatmap_data_shr.index, hovertemplate=hovertemplate_int,
                        colorscale=colorscale, showscale=False, zmin=heatmap_data_shr.min().min(), zmax=heatmap_data_shr.max().max()), row=3, col=2)

# Figure 9 - Win Rate
heatmap_data_sor = macd_params_results[macd_params_results["signal"] == unique_signals[0]].pivot(index="fast", columns="slow", values="win_rate")
fig.add_trace(go.Heatmap(z=heatmap_data_sor.values, x=heatmap_data_sor.columns, y=heatmap_data_sor.index, hovertemplate=hovertemplate_pct,
                        colorscale=colorscale, showscale=False, zmin=heatmap_data_sor.min().min(), zmax=heatmap_data_sor.max().max()), row=3, col=3)

# Update axes -
fig.update_xaxes(range=[1.5, max_range + 0.5])
fig.update_yaxes(range=[0.5, max_range])

# Define steps for the slider -
steps = []
for signal in unique_signals:
    heatmap_data_lr = macd_params_results[macd_params_results["signal"] == signal].pivot(index="fast", columns="slow", values="tot_return")
    heatmap_data_ar = macd_params_results[macd_params_results["signal"] == signal].pivot(index="fast", columns="slow", values="avg_return")
    heatmap_data_vl = macd_params_results[macd_params_results["signal"] == signal].pivot(index="fast", columns="slow", values="volatility")

    heatmap_data_lrtn = macd_params_results[macd_params_results["signal"] == signal].pivot(index="fast", columns="slow", values="tot_return_to_trade_no")
    heatmap_data_artn = macd_params_results[macd_params_results["signal"] == signal].pivot(index="fast", columns="slow", values="avg_return_to_trade_no")
    heatmap_data_tn = macd_params_results[macd_params_results["signal"] == signal].pivot(index="fast", columns="slow", values="trade_no")

    heatmap_data_dd = macd_params_results[macd_params_results["signal"] == signal].pivot(index="fast", columns="slow", values="max_drawdown")
    heatmap_data_shr = macd_params_results[macd_params_results["signal"] == signal].pivot(index="fast", columns="slow", values="sharpe_ratio")
    heatmap_data_sor = macd_params_results[macd_params_results["signal"] == signal].pivot(index="fast", columns="slow", values="win_rate")

    step = dict(
        method="update",
        args=[{"z": [heatmap_data_lr.values, heatmap_data_ar.values, heatmap_data_vl.values,
                     heatmap_data_lrtn.values, heatmap_data_artn.values, heatmap_data_tn.values,
                     heatmap_data_dd.values, heatmap_data_shr.values, heatmap_data_sor.values]}],
        label=str(signal)
    )
    steps.append(step)

# Update layout -
fig.update_layout(

    title=f"Heatmap of Strategy Parameters and Results - {company_info['longName']}",
    title_font_family=f_black,
    title_font_size=20,

    title_subtitle_text=f"Ticker: {ticker}  |  Period: {period_info[period]}  |  Interval: {interval_info[interval]}",
    title_subtitle_font_family=f_bold,
    title_subtitle_font_color="gray",
    title_subtitle_font_size=16,

    title_x=0.41,
    title_y=0.975,

    yaxis1_title="<b>Fast EMA</b>",
    yaxis4_title="<b>Fast EMA</b>",
    yaxis7_title="<b>Fast EMA</b>",

    xaxis7_title="<b>Slow EMA</b>",
    xaxis8_title="<b>Slow EMA</b>",
    xaxis9_title="<b>Slow EMA</b>",

    sliders=[{"active": 0,
              "currentvalue": {"prefix": "<b>Signal MA: </b>", "font": {"size": 14}},
              "pad": {"t": 50, "r": 0},
              "steps": steps,
              }],

    autosize=False,
    height=900, width=1000,

    font=dict(family=f_family),
    template="simple_white",
    margin=dict(l=40, r=240, t=120, b=40)
)

# Annotation -
annotation_paragraphs = [
    "<b>Total Return:</b><br>"
    "The final cumulative return from the strategy over the backtest period. It tells us how much the strategy would have made (or lost) if we held it throughout.",
    
    "<b>Average Return</b><br>"
    "The average of all strategy returns per position. It gives a sense of the strategy's average performance per position.",
    
    "<b>Volatility</b><br>"
    "The standard deviation of average returns per position. It measures how much the strategy's returns fluctuate (higher = more risk).",
    
    "<b>Last Return / Trade No</b><br>"
    "Final return divided by the number of trades. It measures the efficiency of the strategy (how much return we're getting per trade).",
    
    "<b>Average Return / Trade No</b><br>"
    "Average return divided by the number of trades. It is similar to the above but looks at the average performance instead of final result.",
    
    "<b>Trade Number</b><br>"
    "Total number of trades executed by the strategy. It helps us understand how active the strategy is (high frequency or low frequency).",
    
    "<b>Drawdown</b><br>"
    "The largest peak-to-trough drop in the strategy's value. It shows the worst dip the portfolio experienced, important for risk management.",
    
    "<b>Sharpe Ratio</b><br>"
    "(Average Return - Risk-Free Rate) / Volatility. Standard metric for risk-adjusted return (higher = better returns per unit of risk).",
    
    "<b>Win Rate</b><br>"
    "Winning Trades / Total Trades. Intuitive and helps understand trade quality, especially for discretionary or short-term strategies."
]

wrapped_annotation_text = "<br><br>".join(
    "<br>".join(textwrap.wrap(p, width=40)) for p in annotation_paragraphs
)

fig.add_annotation(
    text=wrapped_annotation_text,
    xref="paper", yref="paper",
    x=1.33, y=1.15,
    showarrow=False,
    align="left",
    font=dict(size=11)
)

# Show the figure -
fig.show()

# Save the figure as an HTML file
with open("Charts/heatmap.html", "w") as f:
    f.write(css + to_html(fig, include_plotlyjs="cdn", full_html=True))

In [40]:
# Optimisation (filters)

# Filter out and order the strategies based on own preference
best_params = macd_params_results.loc[
    (macd_params_results["trade_no"] < 54) &
    (macd_params_results["max_drawdown"] > -0.25) &
    (macd_params_results["win_rate"] > 0.5)
].sort_values(by=["tot_return", "sharpe_ratio"], ascending=[False, False]).reset_index(drop=True).round(4)

display(best_params.head(10))

# Save the results to an Excel file
best_params.head(10).to_excel(f"Tables/{ticker}_{period}_{interval}_macd_results.xlsx", index=False)

fast  slow  signal  tot_return  avg_return  volatility  trade_no  \
0     4    12      13      0.5131      0.0375      0.0779      25.0   
1     4    13      12      0.5131      0.0375      0.0779      25.0   
2    12    13       4      0.5131      0.0375      0.0779      25.0   
3     4    10      17      0.4684      0.0347      0.0732      25.0   
4     4    11      15      0.4684      0.0347      0.0732      25.0   
5     4    12      14      0.4684      0.0347      0.0732      25.0   
6     4    13      13      0.4684      0.0347      0.0732      25.0   
7     4    14      12      0.4684      0.0347      0.0732      25.0   
8     4    15      11      0.4684      0.0347      0.0732      25.0   
9     4    17      10      0.4684      0.0347      0.0732      25.0   

   tot_return_to_trade_no  avg_return_to_trade_no  total_positions  \
0                  0.0205                  0.0015             12.0   
1                  0.0205                  0.0015             12.0   
2                  0.0205                  0.0015             12.0   
3                  0.0187                  0.0014             12.0   
4                  0.0187                  0.0014             12.0   
5                  0.0187                  0.0014             12.0   
6                  0.0187                  0.0014             12.0   
7                  0.0187                  0.0014             12.0   
8                  0.0187                  0.0014             12.0   
9                  0.0187                  0.0014             12.0   

   profitable_positions  losing_positions  max_drawdown  sharpe_ratio  \
0                   7.0               5.0       -0.2408        1.4190   
1                   7.0               5.0       -0.2408        1.4190   
2                   7.0               5.0       -0.2408        1.4190   
3                   7.0               5.0       -0.2408        1.3178   
4                   7.0               5.0       -0.2408        1.3178   
5                   7.0               5.0       -0.2408        1.3178   
6                   7.0               5.0       -0.2408        1.3178   
7                   7.0               5.0       -0.2408        1.3178   
8                   7.0               5.0       -0.2408        1.3178   
9                   7.0               5.0       -0.2408        1.3178   

   win_rate  
0    0.5833  
1    0.5833  
2    0.5833  
3    0.5833  
4    0.5833  
5    0.5833  
6    0.5833  
7    0.5833  
8    0.5833  
9    0.5833